##Fangyuan Deng
##5074
##HW 3

### Get data in and set up X_train, X_test, y_train objects

In [ ]:
#install aimodelshare library
! pip install aimodelshare==0.0.189

In [1]:
# Get competition data
from aimodelshare import download_data
download_data('public.ecr.aws/y2e2a1d6/sst2_competition_data-repository:latest') 


Data downloaded successfully.


In [2]:
# Set up X_train, X_test, and y_train_labels objects
import pandas as pd
import warnings
warnings.simplefilter(action='ignore', category=Warning)

X_train=pd.read_csv("sst2_competition_data/X_train.csv", squeeze=True)
X_test=pd.read_csv("sst2_competition_data/X_test.csv", squeeze=True)

y_train_labels=pd.read_csv("sst2_competition_data/y_train_labels.csv", squeeze=True)

# ohe encode Y data
y_train = pd.get_dummies(y_train_labels)

X_train.head()

0    The Rock is destined to be the 21st Century 's...
1    The gorgeously elaborate continuation of `` Th...
2    Singer/composer Bryan Adams contributes a slew...
3                 Yet the act is still charming here .
4    Whether or not you 're enlightened by any of D...
Name: text, dtype: object

### 1.Discuss the dataset in general terms and describe why building a predictive model using this data might be practically useful.  Who could benefit from a model like this? Explain.

The Stanford Sentiment Treebank (SST) is a dataset that is used for sentiment analysis, specifically in the field of movie reviews. This dataset contains two labels which are "positive" and "negative".

Buiding a predictive model using this data might be practically useful because sentiment analysis is a valuable tool in market research and customer feedback analysis. Companies use predictive model to learn how their customers view their products.

Companies could benefit from this model. By analyzing the sentiment of movie reviews, companies can identify areas for improvement and make informed decisions about their marketing stategies. Customers can also benefit from this model. They can use the predictions to decide which movie to watch and which not to.

### Preprocess data using keras tokenizer / Write and Save Preprocessor function

In [29]:
# This preprocessor function makes use of the tf.keras tokenizer

from tensorflow import keras
from tensorflow.keras.preprocessing.text import Tokenizer
from tensorflow.keras.utils import pad_sequences
import numpy as np

# Build vocabulary from training text data
tokenizer = Tokenizer(num_words=10000)
tokenizer.fit_on_texts(X_train)

# preprocessor tokenizes words and makes sure all documents have the same length
def preprocessor(data, maxlen=40, max_words=10000):

    sequences = tokenizer.texts_to_sequences(data)

    word_index = tokenizer.word_index
    X = pad_sequences(sequences, maxlen=maxlen)

    return X

print(preprocessor(X_train).shape)
print(preprocessor(X_test).shape)

(6920, 40)
(1821, 40)


### 2. Run at least three prediction models to try to predict the SST sentiment dataset well.

#### 1) Use an Embedding layer and LSTM layers in at least one model

In [4]:
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import Dense, Embedding, LSTM, Flatten

model1 = Sequential()
model1.add(Embedding(10000, 10, input_length=40))
model1.add(LSTM(16, return_sequences=True, dropout=0.2))
model1.add(LSTM(16, dropout=0.2))
model1.add(Flatten())
model1.add(Dense(2, activation='softmax'))

model1.compile(optimizer='rmsprop', loss='binary_crossentropy', metrics=['acc'])
history = model1.fit(preprocessor(X_train), y_train,
                    epochs=5,
                    batch_size=32,
                    validation_split=0.2)

Epoch 1/5
173/173 [==============================] - 10s 37ms/step - loss: 0.6643 - acc: 0.6143 - val_loss: 0.9091 - val_acc: 0.1488
Epoch 2/5
173/173 [==============================] - 7s 43ms/step - loss: 0.5674 - acc: 0.6965 - val_loss: 0.7307 - val_acc: 0.5889
Epoch 3/5
173/173 [==============================] - 6s 37ms/step - loss: 0.4368 - acc: 0.8111 - val_loss: 0.7266 - val_acc: 0.6358
Epoch 4/5
173/173 [==============================] - 5s 31ms/step - loss: 0.3633 - acc: 0.8465 - val_loss: 0.7300 - val_acc: 0.6785
Epoch 5/5
173/173 [==============================] - 7s 40ms/step - loss: 0.3078 - acc: 0.8696 - val_loss: 0.6208 - val_acc: 0.7449


#### Save preprocessor function to local "preprocessor.zip" file

In [5]:
import aimodelshare as ai
ai.export_preprocessor(preprocessor,"") 

Your preprocessor is now saved to 'preprocessor.zip'


#### Save model1 to local ".onnx" file

In [6]:
from aimodelshare.aimsonnx import model_to_onnx

onnx_model = model_to_onnx(model1, framework='keras',
                          transfer_learning=False,
                          deep_learning=True)

with open("model1.onnx", "wb") as f:
    f.write(onnx_model.SerializeToString())

#### Generate predictions from X_test data and submit model to competition

In [7]:
from aimodelshare.aws import set_credentials
    
apiurl="https://rlxjxnoql9.execute-api.us-east-1.amazonaws.com/prod/m" #This is the unique rest api that powers this specific Playground

set_credentials(apiurl=apiurl)

AI Modelshare Username:··········
AI Modelshare Password:··········
AI Model Share login credentials set successfully.


In [8]:
#Instantiate Competition

mycompetition= ai.Competition(apiurl)

In [9]:
#Submit Model 1: 

#-- Generate predicted y values (Model 1)
#Note: Keras predict returns the predicted column index location for classification models
prediction_column_index=model1.predict(preprocessor(X_test)).argmax(axis=1)

# extract correct prediction labels 
prediction_labels = [y_train.columns[i] for i in prediction_column_index]

# Submit Model 1 to Competition Leaderboard
mycompetition.submit_model(model_filepath = "model1.onnx",
                                 preprocessor_filepath="preprocessor.zip",
                                 prediction_submission=prediction_labels,
                           custom_metadata={"team":"9"})

57/57 [==============================] - 2s 10ms/step
Insert search tags to help users find your model (optional): model1
Provide any useful notes about your model (optional): model 1

Your model has been submitted as model version 167

To submit code used to create this model or to view current leaderboard navigate to Model Playground: 

 https://www.modelshare.org/detail/model:2763


In [10]:
# Get leaderboard to explore current best model architectures

# Get raw data in pandas data frame
data = mycompetition.get_leaderboard()

# Stylize leaderboard data
mycompetition.stylize_leaderboard(data)

#### 2)Use an Embedding layer and Conv1d layers in at least one model

In [12]:
from tensorflow.keras.models import Sequential
from tensorflow.keras import layers
from tensorflow.keras.optimizers import RMSprop
from tensorflow.keras.layers import SimpleRNN, LSTM, Embedding, Conv1D, MaxPooling1D, GlobalMaxPooling1D

model2 = Sequential()
model2.add(Embedding(10000, 10, input_length=40))
model2.add(Conv1D(32, 3, activation='relu')) 
model2.add(MaxPooling1D(5)) #
model2.add(Conv1D(32, 3, activation='relu'))
model2.add(GlobalMaxPooling1D())
model2.add(Dense(2, activation='softmax'))

model2.compile(optimizer='rmsprop', loss='binary_crossentropy', metrics=['acc'])
history = model2.fit(preprocessor(X_train), y_train,
                    epochs=5,
                    batch_size=32,
                    validation_split=0.2)

Epoch 1/5
173/173 [==============================] - 5s 9ms/step - loss: 0.6654 - acc: 0.6136 - val_loss: 0.8918 - val_acc: 0.1488
Epoch 2/5
173/173 [==============================] - 1s 8ms/step - loss: 0.6295 - acc: 0.6203 - val_loss: 0.8246 - val_acc: 0.3244
Epoch 3/5
173/173 [==============================] - 1s 7ms/step - loss: 0.5282 - acc: 0.7392 - val_loss: 0.6995 - val_acc: 0.6380
Epoch 4/5
173/173 [==============================] - 1s 7ms/step - loss: 0.4154 - acc: 0.8172 - val_loss: 0.7692 - val_acc: 0.6098
Epoch 5/5
173/173 [==============================] - 1s 5ms/step - loss: 0.3358 - acc: 0.8551 - val_loss: 0.7035 - val_acc: 0.6647


In [13]:
# Save keras model to local ONNX file
from aimodelshare.aimsonnx import model_to_onnx

onnx_model = model_to_onnx(model2, framework='keras',
                          transfer_learning=False,
                          deep_learning=True)

with open("model2.onnx", "wb") as f:
    f.write(onnx_model.SerializeToString())

In [14]:
#Submit Model 2: 

#-- Generate predicted y values (Model 2)
prediction_column_index=model2.predict(preprocessor(X_test)).argmax(axis=1)

# extract correct prediction labels 
prediction_labels = [y_train.columns[i] for i in prediction_column_index]

# Submit Model 2 to Competition Leaderboard
mycompetition.submit_model(model_filepath = "model2.onnx",
                                 preprocessor_filepath="preprocessor.zip",
                                 prediction_submission=prediction_labels,
                           custom_metadata={"team":"9"})

57/57 [==============================] - 0s 2ms/step
Insert search tags to help users find your model (optional): model2
Provide any useful notes about your model (optional): model2

Your model has been submitted as model version 170

To submit code used to create this model or to view current leaderboard navigate to Model Playground: 

 https://www.modelshare.org/detail/model:2763


In [15]:
# Get leaderboard to explore current best model architectures

# Get raw data in pandas data frame
data = mycompetition.get_leaderboard()

# Stylize leaderboard data
mycompetition.stylize_leaderboard(data)

#### 3)Use transfer learning with glove embeddings for at least one of these models

In [ ]:
! wget http://nlp.stanford.edu/data/wordvecs/glove.6B.zip

In [17]:
! unzip glove.6B.zip 

Archive:  glove.6B.zip
  inflating: glove.6B.100d.txt       
  inflating: glove.6B.200d.txt       
  inflating: glove.6B.300d.txt       
  inflating: glove.6B.50d.txt        


In [18]:
# Extract embedding data for 100 feature embedding matrix
import os
import numpy as np

glove_dir = os.getcwd()

embeddings_index = {}
f = open(os.path.join(glove_dir, 'glove.6B.100d.txt'))
for line in f:
    values = line.split()
    word = values[0]
    coefs = np.asarray(values[1:], dtype='float32')
    embeddings_index[word] = coefs
f.close()

print('Found %s word vectors.' % len(embeddings_index))

Found 400001 word vectors.


In [31]:
# Build embedding matrix
embedding_dim = 100 # change if you use txt files using larger number of features
max_words=10000

word_index = tokenizer.word_index
embedding_matrix = np.zeros((max_words, embedding_dim))
for word, i in word_index.items():
    embedding_vector = embeddings_index.get(word)
    if i < max_words:
        if embedding_vector is not None:
            # Words not found in embedding index will be all-zeros.
            embedding_matrix[i] = embedding_vector

In [32]:
# Set up same model architecture as before and then import Glove weights to Embedding layer:
import tensorflow as tf

model3 = tf.keras.Sequential()
model3.add(tf.keras.layers.Embedding(max_words, embedding_dim, input_length=40))
model3.add(tf.keras.layers.Flatten())
model3.add(tf.keras.layers.Dense(32, activation='relu'))
model3.add(tf.keras.layers.Dense(2, activation='softmax'))
model3.summary()

Model: "sequential_4"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 embedding_4 (Embedding)     (None, 40, 100)           1000000   
                                                                 
 flatten_2 (Flatten)         (None, 4000)              0         
                                                                 
 dense_4 (Dense)             (None, 32)                128032    
                                                                 
 dense_5 (Dense)             (None, 2)                 66        
                                                                 
Total params: 1,128,098
Trainable params: 1,128,098
Non-trainable params: 0
_________________________________________________________________


In [34]:
# Add weights in same manner as transfer learning and turn of trainable option before fitting model to freeze weights.
model3.layers[0].set_weights([embedding_matrix])
model3.layers[0].trainable = False



model3.compile(optimizer='rmsprop',
              loss='binary_crossentropy',
              metrics=['acc'])
history = model3.fit(preprocessor(X_train), y_train,
                    epochs=5,
                    batch_size=32,
                    validation_split=0.2)
model3.save_weights('pre_trained_glove_model.h5')

Epoch 1/5
173/173 [==============================] - 2s 9ms/step - loss: 0.3548 - acc: 0.8418 - val_loss: 1.0268 - val_acc: 0.5181
Epoch 2/5
173/173 [==============================] - 1s 8ms/step - loss: 0.2811 - acc: 0.8905 - val_loss: 0.8618 - val_acc: 0.6380
Epoch 3/5
173/173 [==============================] - 1s 8ms/step - loss: 0.2216 - acc: 0.9191 - val_loss: 1.2124 - val_acc: 0.5065
Epoch 4/5
173/173 [==============================] - 1s 8ms/step - loss: 0.1687 - acc: 0.9447 - val_loss: 1.2569 - val_acc: 0.5636
Epoch 5/5
173/173 [==============================] - 1s 7ms/step - loss: 0.1285 - acc: 0.9594 - val_loss: 0.8059 - val_acc: 0.7283


In [35]:
# Save keras model to local ONNX file
from aimodelshare.aimsonnx import model_to_onnx

onnx_model = model_to_onnx(model3, framework='keras',
                          transfer_learning=True,
                          deep_learning=True)

with open("model3.onnx", "wb") as f:
    f.write(onnx_model.SerializeToString())

In [36]:
#Submit Model 3: 

#-- Generate predicted y values (Model 3)
prediction_column_index=model3.predict(preprocessor(X_test)).argmax(axis=1)

# extract correct prediction labels 
prediction_labels = [y_train.columns[i] for i in prediction_column_index]

# Submit Model 3 to Competition Leaderboard
mycompetition.submit_model(model_filepath = "model3.onnx",
                                 preprocessor_filepath="preprocessor.zip",
                                 prediction_submission=prediction_labels,
                           custom_metadata={"team":"9"})

57/57 [==============================] - 0s 3ms/step
Insert search tags to help users find your model (optional): model3
Provide any useful notes about your model (optional): model3

Your model has been submitted as model version 179

To submit code used to create this model or to view current leaderboard navigate to Model Playground: 

 https://www.modelshare.org/detail/model:2763


In [37]:
# Get leaderboard to explore current best model architectures

# Get raw data in pandas data frame
data = mycompetition.get_leaderboard()

# Stylize leaderboard data
mycompetition.stylize_leaderboard(data)

#### Discuss which models performed better and point out relevant hyper-parameter values for successful models.

The model using an Embedding layer and LSTM layers performed better. In that model, I set max_words to 10000, features to 10, and max_lenth to 40 in Embedding layer. Then I add two LSTM layers, with 16 hidden nodes in each LSTM layer. I set epoch to 5 and batch size to 32.

### 3.Fit and submit up to three more models after learning from your team.

After learning from my team, I plan to increase epochs and add more LSTM hidden nodes based on my first model.

In [38]:
model4 = Sequential()
model4.add(Embedding(10000, 10, input_length=40))
model4.add(LSTM(32, return_sequences=True, dropout=0.2))
model4.add(LSTM(32, dropout=0.2))
model4.add(Flatten())
model4.add(Dense(2, activation='softmax'))

model4.compile(optimizer='rmsprop', loss='binary_crossentropy', metrics=['acc'])
history = model4.fit(preprocessor(X_train), y_train,
                    epochs=10,
                    batch_size=32,
                    validation_split=0.2)

Epoch 1/10
173/173 [==============================] - 14s 57ms/step - loss: 0.6624 - acc: 0.6140 - val_loss: 0.7152 - val_acc: 0.4827
Epoch 2/10
173/173 [==============================] - 6s 34ms/step - loss: 0.5377 - acc: 0.7348 - val_loss: 1.0886 - val_acc: 0.4357
Epoch 3/10
173/173 [==============================] - 8s 45ms/step - loss: 0.4068 - acc: 0.8206 - val_loss: 0.6273 - val_acc: 0.7110
Epoch 4/10
173/173 [==============================] - 8s 45ms/step - loss: 0.3374 - acc: 0.8528 - val_loss: 0.5690 - val_acc: 0.7500
Epoch 5/10
173/173 [==============================] - 6s 34ms/step - loss: 0.2925 - acc: 0.8737 - val_loss: 0.8684 - val_acc: 0.5954
Epoch 6/10
173/173 [==============================] - 9s 51ms/step - loss: 0.2532 - acc: 0.8940 - val_loss: 0.5556 - val_acc: 0.7399
Epoch 7/10
173/173 [==============================] - 7s 39ms/step - loss: 0.2233 - acc: 0.9062 - val_loss: 0.5886 - val_acc: 0.7449
Epoch 8/10
173/173 [==============================] - 6s 37ms/step -

In [39]:
# Save keras model to local ONNX file
from aimodelshare.aimsonnx import model_to_onnx

onnx_model = model_to_onnx(model4, framework='keras',
                          transfer_learning=False,
                          deep_learning=True)

with open("model4.onnx", "wb") as f:
    f.write(onnx_model.SerializeToString())

In [40]:
#Submit Model 4: 

#-- Generate predicted y values (Model 4)
prediction_column_index=model4.predict(preprocessor(X_test)).argmax(axis=1)

# extract correct prediction labels 
prediction_labels = [y_train.columns[i] for i in prediction_column_index]

# Submit Model 4 to Competition Leaderboard
mycompetition.submit_model(model_filepath = "model4.onnx",
                                 preprocessor_filepath="preprocessor.zip",
                                 prediction_submission=prediction_labels,
                           custom_metadata={"team":"9"})

57/57 [==============================] - 2s 15ms/step
Insert search tags to help users find your model (optional): model4
Provide any useful notes about your model (optional): model4

Your model has been submitted as model version 183

To submit code used to create this model or to view current leaderboard navigate to Model Playground: 

 https://www.modelshare.org/detail/model:2763


In [41]:
# Get leaderboard to explore current best model architectures

# Get raw data in pandas data frame
data = mycompetition.get_leaderboard()

# Stylize leaderboard data
mycompetition.stylize_leaderboard(data)

Then I will try a bidirectional LSTM in the next model.

In [42]:
from tensorflow.keras.layers import Embedding, Bidirectional

model5 = Sequential()
model5.add(Embedding(10000, 10, input_length=40))
model5.add(Bidirectional(LSTM(32)))
model5.add(Dense(2, activation='softmax'))

model5.compile(optimizer='rmsprop', loss='binary_crossentropy', metrics=['acc'])
history = model5.fit(preprocessor(X_train), y_train,
                    epochs=10,
                    batch_size=32,
                    validation_split=0.2)

Epoch 1/10
173/173 [==============================] - 9s 34ms/step - loss: 0.6636 - acc: 0.6142 - val_loss: 0.8461 - val_acc: 0.1496
Epoch 2/10
173/173 [==============================] - 8s 47ms/step - loss: 0.5101 - acc: 0.7502 - val_loss: 0.5192 - val_acc: 0.8085
Epoch 3/10
173/173 [==============================] - 7s 42ms/step - loss: 0.3654 - acc: 0.8465 - val_loss: 0.4862 - val_acc: 0.7991
Epoch 4/10
173/173 [==============================] - 11s 65ms/step - loss: 0.2805 - acc: 0.8828 - val_loss: 0.5620 - val_acc: 0.7594
Epoch 5/10
173/173 [==============================] - 6s 33ms/step - loss: 0.2297 - acc: 0.9070 - val_loss: 0.5211 - val_acc: 0.7630
Epoch 6/10
173/173 [==============================] - 5s 27ms/step - loss: 0.1977 - acc: 0.9221 - val_loss: 0.4958 - val_acc: 0.7926
Epoch 7/10
173/173 [==============================] - 7s 38ms/step - loss: 0.1677 - acc: 0.9342 - val_loss: 0.8321 - val_acc: 0.7153
Epoch 8/10
173/173 [==============================] - 7s 42ms/step -

In [43]:
# Save keras model to local ONNX file
from aimodelshare.aimsonnx import model_to_onnx

onnx_model = model_to_onnx(model5, framework='keras',
                          transfer_learning=False,
                          deep_learning=True)

with open("model5.onnx", "wb") as f:
    f.write(onnx_model.SerializeToString())

In [44]:
#Submit Model 5: 

#-- Generate predicted y values (Model 5)
prediction_column_index=model5.predict(preprocessor(X_test)).argmax(axis=1)

# extract correct prediction labels 
prediction_labels = [y_train.columns[i] for i in prediction_column_index]

# Submit Model 5 to Competition Leaderboard
mycompetition.submit_model(model_filepath = "model5.onnx",
                                 preprocessor_filepath="preprocessor.zip",
                                 prediction_submission=prediction_labels,
                           custom_metadata={"team":"9"})

57/57 [==============================] - 1s 9ms/step
Insert search tags to help users find your model (optional): model5
Provide any useful notes about your model (optional): model5

Your model has been submitted as model version 184

To submit code used to create this model or to view current leaderboard navigate to Model Playground: 

 https://www.modelshare.org/detail/model:2763


In [45]:
# Get leaderboard to explore current best model architectures

# Get raw data in pandas data frame
data = mycompetition.get_leaderboard()

# Stylize leaderboard data
mycompetition.stylize_leaderboard(data)

Then I want to try a stacked sequential layers.

In [46]:
model6 = Sequential()
model6.add(Embedding(10000, 10, input_length=40))
model6.add(LSTM(32, return_sequences=True))
model6.add(SimpleRNN(16, return_sequences=True))
model6.add(SimpleRNN(16, return_sequences=True))
model6.add(SimpleRNN(16))
model6.add(Dense(2, activation='softmax'))

model6.compile(optimizer='rmsprop', loss='binary_crossentropy', metrics=['acc'])
history = model6.fit(preprocessor(X_train), y_train,
                    epochs=5,
                    batch_size=32,
                    validation_split=0.2)

Epoch 1/5
173/173 [==============================] - 13s 54ms/step - loss: 0.6641 - acc: 0.6160 - val_loss: 0.9107 - val_acc: 0.3345
Epoch 2/5
173/173 [==============================] - 9s 55ms/step - loss: 0.5326 - acc: 0.7370 - val_loss: 0.6164 - val_acc: 0.6655
Epoch 3/5
173/173 [==============================] - 11s 62ms/step - loss: 0.3770 - acc: 0.8416 - val_loss: 0.7016 - val_acc: 0.6691
Epoch 4/5
173/173 [==============================] - 12s 66ms/step - loss: 0.2862 - acc: 0.8819 - val_loss: 0.6904 - val_acc: 0.6597
Epoch 5/5
173/173 [==============================] - 8s 46ms/step - loss: 0.2131 - acc: 0.9176 - val_loss: 0.6183 - val_acc: 0.7247


In [47]:
# Save keras model to local ONNX file
from aimodelshare.aimsonnx import model_to_onnx

onnx_model = model_to_onnx(model6, framework='keras',
                          transfer_learning=False,
                          deep_learning=True)

with open("model6.onnx", "wb") as f:
    f.write(onnx_model.SerializeToString())

In [48]:
#Submit Model 6: 

#-- Generate predicted y values (Model 6)
prediction_column_index=model6.predict(preprocessor(X_test)).argmax(axis=1)

# extract correct prediction labels 
prediction_labels = [y_train.columns[i] for i in prediction_column_index]

# Submit Model 6 to Competition Leaderboard
mycompetition.submit_model(model_filepath = "model6.onnx",
                                 preprocessor_filepath="preprocessor.zip",
                                 prediction_submission=prediction_labels,
                           custom_metadata={"team":"9"})

57/57 [==============================] - 2s 13ms/step
Insert search tags to help users find your model (optional): model 6
Provide any useful notes about your model (optional): model6

Your model has been submitted as model version 185

To submit code used to create this model or to view current leaderboard navigate to Model Playground: 

 https://www.modelshare.org/detail/model:2763


In [49]:
# Get leaderboard to explore current best model architectures

# Get raw data in pandas data frame
data = mycompetition.get_leaderboard()

# Stylize leaderboard data
mycompetition.stylize_leaderboard(data)

### Discuss which models you tried and which models performed better and point out relevant hyper-parameter values for successful models.


After learning from my team, I tried bidirectional LSTM model and stacked sequential model. Bidirectional LSTM model preformed the best. In that model, I set max words to 10000, features to 10, and max lenth to 40 in the Embedding layer, which is same as before. Then I add a bidirectional LSTM layer with 32 hidden nodes. I set epochs to 10 and batch size to 32. It performed very well.